In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install h5py
!pip install typing-extensions
!pip install wheel
!pip install folium==0.2.1
!pip install markupsafe==2.0.1
!pip install -U pandas-profiling
!pip install catboost
!pip install pycaret==2.3.10 markupsafe==2.0.1 pyyaml==5.4.1 -qq

In [59]:
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
import sklearn
import sys
import seaborn as sns
import random as rn
import os
import scipy.stats as stats
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
import pandas_profiling

from sklearn.model_selection import GridSearchCV, cross_val_score, RepeatedKFold
from sklearn import metrics

from sklearn.linear_model import ElasticNet
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier, VotingClassifier

from collections import Counter
from flaml import AutoML

import warnings
%matplotlib inline
warnings.filterwarnings(action='ignore')

In [11]:
%cd '/content/drive/MyDrive/Travel_product_application/'

/content/drive/MyDrive/Travel_product_application


In [12]:
# reproducibility
def set_seed(seed_num):
  # tf.random.set_seed(seed_num)
  np.random.seed(seed_num)
  rn.seed(seed_num)
  os.environ['PYTHONHASHSEED']=str(seed_num)

seed_num = 42
set_seed(seed_num)

## **1. Load dataset**
- id : 샘플 아이디 | Age : 나이 | TypeofContact : 고객의 제품 인지 방법 (회사의 홍보 or 스스로 검색)
- CityTier : 주거 중인 도시의 등급. (인구, 시설, 생활 수준 기준) (1등급 > 2등급 > 3등급) 
- DurationOfPitch : 영업 사원이 고객에게 제공하는 프레젠테이션 기간
- Occupation : 직업 | Gender : 성별 | NumberOfPersonVisiting : 고객과 함께 여행을 계획 중인 총 인원
- NumberOfFollowups : 영업 사원의 프레젠테이션 후 이루어진 후속 조치 수 | ProductPitched : 영업 사원이 제시한 상품
- PreferredPropertyStar : 선호 호텔 숙박업소 등급 | MaritalStatus : 결혼여부
- NumberOfTrips : 평균 연간 여행 횟수 | Passport : 여권 보유 여부 (0: 없음, 1: 있음)
- PitchSatisfactionScore : 영업 사원의 프레젠테이션 만족도 | OwnCar : 자동차 보유 여부 (0: 없음, 1: 있음)
- NumberOfChildrenVisiting : 함께 여행을 계획 중인 5세 미만의 어린이 수
 | Designation : (직업의) 직급
- MonthlyIncome : 월 급여 | **ProdTaken : 여행 패키지 신청 여부 (0: 신청 안 함, 1: 신청함)**

In [13]:
train = pd.read_csv('dataset/train.csv')
test = pd.read_csv('dataset/test.csv')

train.head()

id   Age    TypeofContact  CityTier  DurationOfPitch      Occupation  \
0   1  28.0  Company Invited         1             10.0  Small Business   
1   2  34.0     Self Enquiry         3              NaN  Small Business   
2   3  45.0  Company Invited         1              NaN        Salaried   
3   4  29.0  Company Invited         1              7.0  Small Business   
4   5  42.0     Self Enquiry         3              6.0        Salaried   

   Gender  NumberOfPersonVisiting  NumberOfFollowups ProductPitched  \
0    Male                       3                4.0          Basic   
1  Female                       2                4.0         Deluxe   
2    Male                       2                3.0         Deluxe   
3    Male                       3                5.0          Basic   
4    Male                       2                3.0         Deluxe   

   PreferredPropertyStar MaritalStatus  NumberOfTrips  Passport  \
0                    3.0       Married            3.0         0   
1                    4.0        Single            1.0         1   
2                    4.0       Married            2.0         0   
3                    4.0       Married            3.0         0   
4                    3.0      Divorced            2.0         0   

   PitchSatisfactionScore  OwnCar  NumberOfChildrenVisiting Designation  \
0                       1       0                       1.0   Executive   
1                       5       1                       0.0     Manager   
2                       4       1                       0.0     Manager   
3                       4       0                       1.0   Executive   
4                       3       1                       0.0     Manager   

   MonthlyIncome  ProdTaken  
0        20384.0          0  
1        19599.0          1  
2            NaN          0  
3        21274.0          1  
4        19907.0          0

In [14]:
pr = train.profile_report()
pr.to_file('pr_report.html')
pr

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [15]:
train.isnull().sum()

id                            0
Age                          94
TypeofContact                10
CityTier                      0
DurationOfPitch             102
Occupation                    0
Gender                        0
NumberOfPersonVisiting        0
NumberOfFollowups            13
ProductPitched                0
PreferredPropertyStar        10
MaritalStatus                 0
NumberOfTrips                57
Passport                      0
PitchSatisfactionScore        0
OwnCar                        0
NumberOfChildrenVisiting     27
Designation                   0
MonthlyIncome               100
ProdTaken                     0
dtype: int64

In [16]:
test.isnull().sum()

id                            0
Age                         132
TypeofContact                15
CityTier                      0
DurationOfPitch             149
Occupation                    0
Gender                        0
NumberOfPersonVisiting        0
NumberOfFollowups            32
ProductPitched                0
PreferredPropertyStar        16
MaritalStatus                 0
NumberOfTrips                83
Passport                      0
PitchSatisfactionScore        0
OwnCar                        0
NumberOfChildrenVisiting     39
Designation                   0
MonthlyIncome               133
dtype: int64

In [87]:
print(train.shape)
print(test.shape)

(1955, 20)
(2933, 19)


In [88]:
df_train = train.copy()
df_test = test.copy()

## **2. Make dataset**

In [89]:
df_train = df_train.fillna(df_train.mean())
df_test = df_test.fillna(df_test.mean())

In [90]:
df_train.isnull().sum()

id                           0
Age                          0
TypeofContact               10
CityTier                     0
DurationOfPitch              0
Occupation                   0
Gender                       0
NumberOfPersonVisiting       0
NumberOfFollowups            0
ProductPitched               0
PreferredPropertyStar        0
MaritalStatus                0
NumberOfTrips                0
Passport                     0
PitchSatisfactionScore       0
OwnCar                       0
NumberOfChildrenVisiting     0
Designation                  0
MonthlyIncome                0
ProdTaken                    0
dtype: int64

In [91]:
df_test.isnull().sum()

id                           0
Age                          0
TypeofContact               15
CityTier                     0
DurationOfPitch              0
Occupation                   0
Gender                       0
NumberOfPersonVisiting       0
NumberOfFollowups            0
ProductPitched               0
PreferredPropertyStar        0
MaritalStatus                0
NumberOfTrips                0
Passport                     0
PitchSatisfactionScore       0
OwnCar                       0
NumberOfChildrenVisiting     0
Designation                  0
MonthlyIncome                0
dtype: int64

In [92]:
df_train['TypeofContact'].value_counts()

Self Enquiry       1379
Company Invited     566
Name: TypeofContact, dtype: int64

In [93]:
df_train['TypeofContact'] = df_train['TypeofContact'].fillna('Self Enquiry')
df_test['TypeofContact'] = df_test['TypeofContact'].fillna('Self Enquiry')

In [94]:
df_train.isnull().sum()

id                          0
Age                         0
TypeofContact               0
CityTier                    0
DurationOfPitch             0
Occupation                  0
Gender                      0
NumberOfPersonVisiting      0
NumberOfFollowups           0
ProductPitched              0
PreferredPropertyStar       0
MaritalStatus               0
NumberOfTrips               0
Passport                    0
PitchSatisfactionScore      0
OwnCar                      0
NumberOfChildrenVisiting    0
Designation                 0
MonthlyIncome               0
ProdTaken                   0
dtype: int64

In [95]:
df_test.isnull().sum()

id                          0
Age                         0
TypeofContact               0
CityTier                    0
DurationOfPitch             0
Occupation                  0
Gender                      0
NumberOfPersonVisiting      0
NumberOfFollowups           0
ProductPitched              0
PreferredPropertyStar       0
MaritalStatus               0
NumberOfTrips               0
Passport                    0
PitchSatisfactionScore      0
OwnCar                      0
NumberOfChildrenVisiting    0
Designation                 0
MonthlyIncome               0
dtype: int64

In [96]:
print(df_train.shape)
print(df_test.shape)

(1955, 20)
(2933, 19)


In [97]:
categorical_fts = ['TypeofContact', 'Occupation', 'Gender', 'ProductPitched', 'MaritalStatus', 'Passport', 'OwnCar', 'Designation']

In [98]:
for i in range(len(categorical_fts)):
  print(categorical_fts[i], ':')
  print(df_train[categorical_fts[i]].unique())

TypeofContact :
['Company Invited' 'Self Enquiry']
Occupation :
['Small Business' 'Salaried' 'Large Business' 'Free Lancer']
Gender :
['Male' 'Female' 'Fe Male']
ProductPitched :
['Basic' 'Deluxe' 'King' 'Standard' 'Super Deluxe']
MaritalStatus :
['Married' 'Single' 'Divorced' 'Unmarried']
Passport :
[0 1]
OwnCar :
[0 1]
Designation :
['Executive' 'Manager' 'VP' 'Senior Manager' 'AVP']


In [99]:
df_train['Gender'] = df_train['Gender'].str.replace('Fe Male', 'Female')
df_test['Gender'] = df_test['Gender'].str.replace('Fe Male', 'Female')

In [100]:
print(df_train['Gender'].unique())

['Male' 'Female']


In [101]:
# One-hot encoding
train_data = pd.get_dummies(df_train)
test_data = pd.get_dummies(df_test)

print(train_data.columns)
print(test_data.columns)

Index(['id', 'Age', 'CityTier', 'DurationOfPitch', 'NumberOfPersonVisiting',
       'NumberOfFollowups', 'PreferredPropertyStar', 'NumberOfTrips',
       'Passport', 'PitchSatisfactionScore', 'OwnCar',
       'NumberOfChildrenVisiting', 'MonthlyIncome', 'ProdTaken',
       'TypeofContact_Company Invited', 'TypeofContact_Self Enquiry',
       'Occupation_Free Lancer', 'Occupation_Large Business',
       'Occupation_Salaried', 'Occupation_Small Business', 'Gender_Female',
       'Gender_Male', 'ProductPitched_Basic', 'ProductPitched_Deluxe',
       'ProductPitched_King', 'ProductPitched_Standard',
       'ProductPitched_Super Deluxe', 'MaritalStatus_Divorced',
       'MaritalStatus_Married', 'MaritalStatus_Single',
       'MaritalStatus_Unmarried', 'Designation_AVP', 'Designation_Executive',
       'Designation_Manager', 'Designation_Senior Manager', 'Designation_VP'],
      dtype='object')
Index(['id', 'Age', 'CityTier', 'DurationOfPitch', 'NumberOfPersonVisiting',
       'NumberOfFollo

In [102]:
train_id = train_data['id']
test_id = test_data['id']

train_x = train_data.drop(['id', 'ProdTaken'], axis = 1)
test_x = test_data.drop('id', axis = 1)

train_y = train_data['ProdTaken']

print(train_x.shape)
print(train_y.shape)
print(test_x.shape)

(1955, 34)
(1955,)
(2933, 34)


## **3. Modeling**

In [103]:
MODEL_TIME_BUDGET = 60*5
MODEL_METRIC = 'accuracy'
MODEL_TASK = "classification"
MODEL_LIST = ["lgbm"]

auto_lgbm = AutoML()
params = {
    "time_budget": MODEL_TIME_BUDGET,  
    "metric": MODEL_METRIC,
    "estimator_list": MODEL_LIST, 
    "task": MODEL_TASK,
    "seed":seed_num,
}
auto_lgbm.fit(train_x, train_y, **params)

[flaml.automl: 08-31 09:59:14] {2565} INFO - task = classification
INFO:flaml.automl:task = classification
[flaml.automl: 08-31 09:59:14] {2567} INFO - Data split method: stratified
INFO:flaml.automl:Data split method: stratified
[flaml.automl: 08-31 09:59:14] {2570} INFO - Evaluation method: cv
INFO:flaml.automl:Evaluation method: cv
[flaml.automl: 08-31 09:59:14] {2689} INFO - Minimizing error metric: 1-accuracy
INFO:flaml.automl:Minimizing error metric: 1-accuracy
[flaml.automl: 08-31 09:59:14] {2831} INFO - List of ML learners in AutoML Run: ['lgbm']
INFO:flaml.automl:List of ML learners in AutoML Run: ['lgbm']
[flaml.automl: 08-31 09:59:14] {3133} INFO - iteration 0, current learner lgbm
INFO:flaml.automl:iteration 0, current learner lgbm
[flaml.automl: 08-31 09:59:14] {3267} INFO - Estimated sufficient time budget=1065s. Estimated necessary time budget=1s.
INFO:flaml.automl:Estimated sufficient time budget=1065s. Estimated necessary time budget=1s.
[flaml.automl: 08-31 09:59:14] 

In [107]:
MODEL_TIME_BUDGET = 60*20
MODEL_METRIC = 'accuracy'
MODEL_TASK = "classification"
MODEL_LIST = ["xgboost"]

auto_xgb = AutoML()
params = {
    "time_budget": MODEL_TIME_BUDGET,  
    "metric": MODEL_METRIC,
    "estimator_list": MODEL_LIST, 
    "task": MODEL_TASK,
    "seed":seed_num,
}
auto_xgb.fit(train_x, train_y, **params)

[flaml.automl: 08-31 10:34:04] {2565} INFO - task = classification
INFO:flaml.automl:task = classification
[flaml.automl: 08-31 10:34:04] {2567} INFO - Data split method: stratified
INFO:flaml.automl:Data split method: stratified
[flaml.automl: 08-31 10:34:04] {2570} INFO - Evaluation method: cv
INFO:flaml.automl:Evaluation method: cv
[flaml.automl: 08-31 10:34:04] {2689} INFO - Minimizing error metric: 1-accuracy
INFO:flaml.automl:Minimizing error metric: 1-accuracy
[flaml.automl: 08-31 10:34:04] {2831} INFO - List of ML learners in AutoML Run: ['xgboost']
INFO:flaml.automl:List of ML learners in AutoML Run: ['xgboost']
[flaml.automl: 08-31 10:34:04] {3133} INFO - iteration 0, current learner xgboost
INFO:flaml.automl:iteration 0, current learner xgboost
[flaml.automl: 08-31 10:34:04] {3267} INFO - Estimated sufficient time budget=1558s. Estimated necessary time budget=2s.
INFO:flaml.automl:Estimated sufficient time budget=1558s. Estimated necessary time budget=2s.
[flaml.automl: 08-3

In [105]:
MODEL_TIME_BUDGET = 60*10
MODEL_METRIC = 'accuracy'
MODEL_TASK = "classification"
MODEL_LIST = ["rf"]

auto_rf = AutoML()
params = {
    "time_budget": MODEL_TIME_BUDGET,  
    "metric": MODEL_METRIC,
    "estimator_list": MODEL_LIST, 
    "task": MODEL_TASK,
    "seed":seed_num,
}
auto_rf.fit(train_x, train_y, **params)

[flaml.automl: 08-31 10:14:04] {2565} INFO - task = classification
INFO:flaml.automl:task = classification
[flaml.automl: 08-31 10:14:04] {2567} INFO - Data split method: stratified
INFO:flaml.automl:Data split method: stratified
[flaml.automl: 08-31 10:14:04] {2570} INFO - Evaluation method: cv
INFO:flaml.automl:Evaluation method: cv
[flaml.automl: 08-31 10:14:04] {2689} INFO - Minimizing error metric: 1-accuracy
INFO:flaml.automl:Minimizing error metric: 1-accuracy
[flaml.automl: 08-31 10:14:04] {2831} INFO - List of ML learners in AutoML Run: ['rf']
INFO:flaml.automl:List of ML learners in AutoML Run: ['rf']
[flaml.automl: 08-31 10:14:04] {3133} INFO - iteration 0, current learner rf
INFO:flaml.automl:iteration 0, current learner rf
[flaml.automl: 08-31 10:14:06] {3267} INFO - Estimated sufficient time budget=15670s. Estimated necessary time budget=16s.
INFO:flaml.automl:Estimated sufficient time budget=15670s. Estimated necessary time budget=16s.
[flaml.automl: 08-31 10:14:06] {331

In [106]:
MODEL_TIME_BUDGET = 60*10
MODEL_METRIC = 'accuracy'
MODEL_TASK = "classification"
MODEL_LIST = ["extra_tree"]

auto_ext = AutoML()
params = {
    "time_budget": MODEL_TIME_BUDGET,  
    "metric": MODEL_METRIC,
    "estimator_list": MODEL_LIST, 
    "task": MODEL_TASK,
    "seed":seed_num,
}
auto_ext.fit(train_x, train_y, **params)

[flaml.automl: 08-31 10:24:03] {2565} INFO - task = classification
INFO:flaml.automl:task = classification
[flaml.automl: 08-31 10:24:03] {2567} INFO - Data split method: stratified
INFO:flaml.automl:Data split method: stratified
[flaml.automl: 08-31 10:24:03] {2570} INFO - Evaluation method: cv
INFO:flaml.automl:Evaluation method: cv
[flaml.automl: 08-31 10:24:03] {2689} INFO - Minimizing error metric: 1-accuracy
INFO:flaml.automl:Minimizing error metric: 1-accuracy
[flaml.automl: 08-31 10:24:03] {2831} INFO - List of ML learners in AutoML Run: ['extra_tree']
INFO:flaml.automl:List of ML learners in AutoML Run: ['extra_tree']
[flaml.automl: 08-31 10:24:03] {3133} INFO - iteration 0, current learner extra_tree
INFO:flaml.automl:iteration 0, current learner extra_tree
[flaml.automl: 08-31 10:24:05] {3267} INFO - Estimated sufficient time budget=12234s. Estimated necessary time budget=12s.
INFO:flaml.automl:Estimated sufficient time budget=12234s. Estimated necessary time budget=12s.
[fl

In [108]:
lightgbm = LGBMClassifier(colsample_bytree=0.8733899242408911,
               learning_rate=0.19737872129139739, max_bin=15,
               min_child_samples=18, n_estimators=1541, num_leaves=172,
               reg_alpha=0.0009765625, reg_lambda=0.0402322402391567,
               verbose=-1, seed = seed_num)

lightgbm.fit(train_x, train_y)

LGBMClassifier(colsample_bytree=0.8733899242408911,
               learning_rate=0.19737872129139739, max_bin=15,
               min_child_samples=18, n_estimators=1541, num_leaves=172,
               reg_alpha=0.0009765625, reg_lambda=0.0402322402391567, seed=42,
               verbose=-1)

In [109]:
xgboost = XGBClassifier(colsample_bylevel=1.0, colsample_bytree=0.8757960080874843,
              grow_policy='lossguide', learning_rate=0.018596463469459305,
              max_depth=0, max_leaves=33, min_child_weight=0.2322454444259425,
              n_estimators=1807, n_jobs=-1, reg_alpha=0.002680230868610329,
              reg_lambda=0.0009765625, subsample=0.8135337528547746,
              tree_method='hist', use_label_encoder=False, verbosity=0, seed = seed_num)

xgboost.fit(train_x, train_y)

XGBClassifier(colsample_bylevel=1.0, colsample_bytree=0.8757960080874843,
              grow_policy='lossguide', learning_rate=0.018596463469459305,
              max_depth=0, max_leaves=33, min_child_weight=0.2322454444259425,
              n_estimators=1807, n_jobs=-1, reg_alpha=0.002680230868610329,
              reg_lambda=0.0009765625, seed=42, subsample=0.8135337528547746,
              tree_method='hist', use_label_encoder=False, verbosity=0)

In [112]:
rf = RandomForestClassifier(max_features=0.6795142144725661, max_leaf_nodes=186,
                       n_estimators=25, n_jobs=-1, random_state = seed_num)

rf.fit(train_x, train_y)

RandomForestClassifier(max_features=0.6795142144725661, max_leaf_nodes=186,
                       n_estimators=25, n_jobs=-1, random_state=42)

In [113]:
ext = ExtraTreesClassifier(criterion='entropy', max_features=0.32960779717230204,
                     max_leaf_nodes=368, n_estimators=89, n_jobs=-1, random_state = seed_num)

ext.fit(train_x, train_y)

ExtraTreesClassifier(criterion='entropy', max_features=0.32960779717230204,
                     max_leaf_nodes=368, n_estimators=89, n_jobs=-1,
                     random_state=42)

- Hard voting

In [114]:
print(test_x.shape)

(2933, 34)


In [115]:
lgb_p = lightgbm.predict(test_x)
xgb_p = xgboost.predict(test_x)
rf_p = rf.predict(test_x)
ext_p = ext.predict(test_x)

In [116]:
def mode(list):
    count = 0
    mode = 0;
    for x in list: 
        if list.count(x) > count:
            count = list.count(x)
            mode = x

    return mode

In [121]:
prediction = []
for i in range(0, len(lgb_p)):
    prediction.append(mode([lgb_p[i], xgb_p[i], rf_p[i], ext_p[i]]))
    # prediction.append(mode([lgb_p[i], xgb_p[i]]))

print(prediction)

[0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 

In [122]:
sample_submission = pd.read_csv('dataset/sample_submission.csv')
sample_submission['ProdTaken'] = prediction

sample_submission.to_csv('hard_vt2.csv',index = False)

In [123]:
sample_submission.head()

id  ProdTaken
0   1          0
1   2          0
2   3          0
3   4          0
4   5          1